This notebook includes code to build, train and test models using SageMaker's object detection algorithm. Using a notebook as opposed to SageMaker's UI, gives us the advantage of having access to all of the model artifacts in one place and allows us to specify all input data and output locations in a single notebook. 

Code and documentation in this notebook was heavily inspired by the following Object Detection sample notebook created by Amazon SageMaker
https://sagemaker-examples.readthedocs.io/en/latest/introduction_to_amazon_algorithms/object_detection_birds/object_detection_birds.html

We start by identifying the location of the S3 bucket where we have all of our training data. We need to specify the locations for the training and validation sets.

In [1]:
# Imports for the S3 Bucket
import sagemaker
import boto3

# Specifying which S3 Bucket has our training data
s3 = boto3.resource('s3')
bucket = s3.Bucket('sagemaker-us-west-2-959616474350')

# Specifying training and validation channels
train_channel = 'New_Manifest_File.jsonl'
validation_channel = 'New_Manifest_File.jsonl'

# Formatting the exact location of training and validation data
s3_train_data = "s3://sagemaker-us-west-2-959616474350/New_Manifest_File.jsonl"
s3_validation_data = "s3://sagemaker-us-west-2-959616474350/New_Manifest_File.jsonl"

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/boto3/compat.py:88: PythonDeprecationWarning: Boto3 will no longer support Python 3.6 starting May 30, 2022. To continue receiving service updates, bug fixes, and security updates please upgrade to Python 3.7 or later. More information can be found here: https://aws.amazon.com/blogs/developer/python-support-policy-updates-for-aws-sdks-and-tools/
  warnings.warn(warning, PythonDeprecationWarning)


We need to provide proper authentication to allow for the use of Amazon's SageMaker services, so we must specify our execution role from an account with SageMaker access. This also allows for access to the data in the S3 bucket.

In [2]:
# Gets execution role to authenticate usage of SageMaker services and access to S3 bucket
from sagemaker import get_execution_role

role = get_execution_role()
print(role)
sess = sagemaker.Session()

arn:aws:iam::959616474350:role/service-role/AmazonSageMaker-ExecutionRole-20220216T171236


# Model Training

We need to get the URI to the Amazon SageMaker Object Detection docker image. This ensures the estimator uses the correct algorithm from the correct region, which is specified based on the session.

In [3]:
from sagemaker import image_uris

# Retrieves the URI to the object detection docker image
training_image = image_uris.retrieve(
    region=sess.boto_region_name, framework="object-detection", version="latest"
)
print(training_image)

Defaulting to the only supported framework/algorithm version: 1. Ignoring framework/algorithm version: latest.


433757028032.dkr.ecr.us-west-2.amazonaws.com/object-detection:1


We must also specify our desired output location S3 bucket for model artifacts once the model is trained.

In [4]:
# S3 Bucket output location for model artifacts
s3_output_location = "s3://sagemaker-us-west-2-959616474350/output"

Now we can start building the model framework specifying the parameters for the model type including the algorithm, execution role, instance type and output location.

In [6]:
# Building the model framework using a SageMaker estimator object
od_model = sagemaker.estimator.Estimator(
    training_image,
    role,
    instance_count=1,
    instance_type="ml.p3.2xlarge",
    volume_size=50,
    max_run=360000,
    input_mode="Pipe",
    output_path=s3_output_location,
    sagemaker_session=sess,
)

# Set Hyperparameters

Now we define the hyperparameters for our object detection model. At the time of creating this notebook, SageMaker's object detection algorithm supports 2 base networks, the VGG-16 and ResNet-50.

In [9]:
# Function to set hyperparameters for the model
def set_hyperparameters(num_classes, num_training_samples, mini_batch_size, num_epochs, learning_rate, lr_steps,
                        lr_scheduler_factor, base_network="resnet-50", use_pretrained_model = 1, optimizer="sgd", 
                        momentum=0.9, weight_decay=0.0005, overlap_threshold=0.5, nms_threshold=0.45,
                        image_shape=512, label_width=350):
    num_classes = num_classes
    num_training_samples = num_training_samples
    print("num classes: {}, num training images: {}, mini batch size: {}, \n num_epochs: {}, learning rate: {}, lr steps: {}, lr scheduler factor: {}, \n base network: {}, optimizer: {}, momentum: {}, weight decay: {}, \n overlap threshold: {}, nms threshold: {}".format(num_classes, num_training_samples,
                                                           mini_batch_size, num_epochs, learning_rate,
                                                           lr_steps, lr_scheduler_factor, base_network,
                                                           optimizer, momentum, weight_decay,
                                                           overlap_threshold, nms_threshold))

    od_model.set_hyperparameters(
        base_network=base_network,
        use_pretrained_model=use_pretrained_model,
        num_classes=num_classes,
        mini_batch_size=mini_batch_size,
        epochs=num_epochs,
        learning_rate=learning_rate,
        lr_scheduler_step=lr_steps,
        lr_scheduler_factor=lr_scheduler_factor,
        optimizer=optimizer,
        momentum=momentum,
        weight_decay=weight_decay,
        overlap_threshold=overlap_threshold,
        nms_threshold=nms_threshold,
        image_shape=image_shape,
        label_width=label_width,
        num_training_samples=num_training_samples,
    )

In [10]:
# Set hyperparameters
set_hyperparameters(1, 360, 16, 100, 0.001, "33,67", 0.1)

num classes: 1, num training images: 360, mini batch size: 16, 
 num_epochs: 100, learning rate: 0.001, lr steps: 33,67, lr scheduler factor: 0.1, 
 base network: resnet-50, optimizer: sgd, momentum: 0.9, weight decay: 0.0005, 
 overlap threshold: 0.5, nms threshold: 0.45


Before we submit the training job, we must specify our data types and the locations for the data channels. Because we are using PNGs we use the "AugmentedManifestFile" format for our bounding boxes in our S3 bucket and we must specify "RecordIO" for our Record Wrapper and "application/x-image" for our content type.

In [12]:
# Specifying training and validation inputs
train_data = sagemaker.inputs.TrainingInput(
    s3_train_data,
    distribution="FullyReplicated",
    content_type="application/x-recordio",
    record_wrapping="RecordIO",
    s3_data_type="AugmentedManifestFile",
    attribute_names=['source-ref', 'bounding-box']
)
validation_data = sagemaker.inputs.TrainingInput(
    s3_validation_data,
    distribution="FullyReplicated",
    content_type="application/x-recordio",
    record_wrapping="RecordIO",
    s3_data_type="AugmentedManifestFile",
    attribute_names=['source-ref', 'bounding-box']
)
data_channels = {"train": train_data, "validation": validation_data}

Now we can submit the training job using the fit method. Once it is done, we can access model artifacts in the S3 bucket where the output directory was specified previously. 

In [13]:
%%time
# Submitting the training job
od_model.fit(inputs=data_channels, logs=True)

2022-04-25 01:22:28 Starting - Starting the training job...
2022-04-25 01:22:54 Starting - Preparing the instances for trainingProfilerReport-1650849747: InProgress
.........
2022-04-25 01:24:23 Downloading - Downloading input data
2022-04-25 01:24:23 Training - Downloading the training image.........
2022-04-25 01:25:59 Training - Training image download completed. Training in progress..Docker entrypoint called with argument(s): train
Running default environment configuration script
[04/25/2022 01:26:04 INFO 140429843244864 integration.py:636] worker started
[04/25/2022 01:26:04 INFO 140429843244864] Reading default configuration from /opt/amazon/lib/python3.7/site-packages/algorithm/default-input.json: {'base_network': 'vgg-16', 'use_pretrained_model': '0', 'num_classes': '', 'mini_batch_size': '32', 'epochs': '30', 'learning_rate': '0.001', 'lr_scheduler_step': '', 'lr_scheduler_factor': '0.1', 'optimizer': 'sgd', 'momentum': '0.9', 'weight_decay': '0.0005', 'overlap_threshold': '0.

Now that we have trained a model, we take a look at the Mean Average Preciscion (mAP) score, the key object detection metric, to assess how the job progressed on the validation data. Below is code to plot the mAP against the epochs.

In [2]:
import boto3
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker

%matplotlib inline

# Specifying the training log channel
client = boto3.client("logs")
BASE_LOG_NAME = "/aws/sagemaker/TrainingJobs"

# Function to plot the mAP score over time against the epochs
def plot_object_detection_log(model, title):
    logs = client.describe_log_streams(
        logGroupName=BASE_LOG_NAME, logStreamNamePrefix=model._current_job_name
    )
    cw_log = client.get_log_events(
        logGroupName=BASE_LOG_NAME, logStreamName=logs["logStreams"][0]["logStreamName"]
    )

    mAP_accs = []
    for e in cw_log["events"]:
        msg = e["message"]
        if "validation mAP <score>=" in msg:
            num_start = msg.find("(")
            num_end = msg.find(")")
            mAP = msg[num_start + 1 : num_end]
            mAP_accs.append(float(mAP))

    print(title)
    print("Maximum mAP: %f " % max(mAP_accs))

    fig, ax = plt.subplots()
    plt.xlabel("Epochs")
    plt.ylabel("Mean Avg Precision (mAP)")
    (val_plot,) = ax.plot(range(len(mAP_accs)), mAP_accs, label="mAP")
    plt.legend(handles=[val_plot])
    ax.yaxis.set_ticks(np.arange(0.0, 1.05, 0.1))
    ax.yaxis.set_major_formatter(ticker.FormatStrFormatter("%0.2f"))
    plt.show()

In [3]:
# Call function to plot mAP score against epochs
plot_object_detection_log(od_model, "mAP tracking for job: " + od_model._current_job_name)

NameError: name 'od_model' is not defined

# Model Testing (to be changed, still code pulled directly from sample notebook)

Now that our model is fully trained, we now host the model as an Amazon SageMaker real-time hosted endpoint. With that we can run the model on a testing set and make predictions/inferences. Note that we don't need to host the model using the same instance we used to train. The P2/P3 machines we used to train are much more expensive instances, used to perform the compute heavy tasks of model training. Here, we use the less expensive M4 instance to host. To host, we just call the deploy method. **Also note that after deployment, you must delete the endpoint at the end of the notebook to avoid excess charges**

In [ ]:
%%time
object_detector = od_model.deploy(initial_instance_count=1, instance_type="ml.m4.xlarge")

Here we create a function to easily visualize detection outputs. Note that you can filter out low-confidence predictions.

In [ ]:
def visualize_detection(img_file, dets, classes=[], thresh=0.6):
    """
    visualize detections in one image
    Parameters:
    ----------
    img : numpy.array
        image, in bgr format
    dets : numpy.array
        ssd detections, numpy.array([[id, score, x1, y1, x2, y2]...])
        each row is one object
    classes : tuple or list of str
        class names
    thresh : float
        score threshold
    """
    import random
    import matplotlib.pyplot as plt
    import matplotlib.image as mpimg

    img = mpimg.imread(img_file)
    plt.imshow(img)
    height = img.shape[0]
    width = img.shape[1]
    colors = dict()
    num_detections = 0
    for det in dets:
        (klass, score, x0, y0, x1, y1) = det
        if score < thresh:
            continue
        num_detections += 1
        cls_id = int(klass)
        if cls_id not in colors:
            colors[cls_id] = (random.random(), random.random(), random.random())
        xmin = int(x0 * width)
        ymin = int(y0 * height)
        xmax = int(x1 * width)
        ymax = int(y1 * height)
        rect = plt.Rectangle(
            (xmin, ymin),
            xmax - xmin,
            ymax - ymin,
            fill=False,
            edgecolor=colors[cls_id],
            linewidth=3.5,
        )
        plt.gca().add_patch(rect)
        class_name = str(cls_id)
        if classes and len(classes) > cls_id:
            class_name = classes[cls_id]
        print("{},{}".format(class_name, score))
        plt.gca().text(
            xmin,
            ymin - 2,
            "{:s} {:.3f}".format(class_name, score),
            bbox=dict(facecolor=colors[cls_id], alpha=0.5),
            fontsize=12,
            color="white",
        )

    print("Number of detections: " + str(num_detections))
    plt.show()

Now we actually attempt to detect the sounds in the images. Note we need to specify PNG in the content type, since that is the format of our data. The SageMaker endpoint returns a JSON object that we can access and look at. This function will attempt to make detections in a single image, will the return the results of the predictions and visualize them using the previously created visualize_detection() function.

In [ ]:
OBJECT_CATEGORIES = classes_df["class_id"].values.tolist()

# Function to make predictions on new images
def show_hb_prediction(filename, ep, thresh=0.40):
    b = ""
    with open(filename, "rb") as image:
        f = image.read()
        b = bytearray(f)
    endpoint_response = runtime.invoke_endpoint(EndpointName=ep, ContentType="image/jpeg", Body=b)
    results = endpoint_response["Body"].read()
    detections = json.loads(results)
    visualize_detection(filename, detections["prediction"], OBJECT_CATEGORIES, thresh)

In [ ]:
# Function that runs predictions on full testing set
def test_model():
    show_hb_prediction("hummingbird-1.jpg", object_detector.endpoint_name)

test_model()

# Clean Up

Finally, we delete the endpoint once we are done making inferences to avoid additional charges on the account.

In [73]:
# Call to delete endpoint session
sagemaker.Session().delete_endpoint(object_detector.endpoint_name)

NameError: name 'object_detector' is not defined